In [ ]:
!pip install osmnx
!pip install matplotlib networkx shapely geopandas

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.2/100.2 kB 1.3 MB/s eta 0:00:00


In [ ]:
import folium
from shapely.geometry import Polygon
import re

# Input WKT string
# wkt = "POLYGON(([-75.84147 45.350909], [-75.849642 45.353404], [-75.848056 45.355969], [-75.839884 45.353473], [-75.84147 45.350909]))"
# wkt = "POLYGON(([-75.6785041441 45.4229219962], [-75.6809760671 45.4260785123], [-75.6769453678 45.4276333175], [-75.6744734448 45.4244768883], [-75.6785041441 45.4229219962]))"

# wkt = "POLYGON(([-75.70509 45.419686], [-75.706894 45.42199], [-75.702864 45.423545], [-75.70106 45.421241], [-75.70509 45.419686]))"

# wkt = "POLYGON(([-75.6999911313 45.4161493202], [-75.701882746 45.4184179291], [-75.6977063607 45.4201336873], [-75.695814746 45.4178651473], [-75.6999911313 45.4161493202]))"

# wkt = "POLYGON(([-75.6765845296 45.4214748976], [-75.679271806 45.4246974104], [-75.6750954207 45.4264129778], [-75.6724081443 45.4231905629], [-75.6765845296 45.4214748976]))"
wkt = "POLYGON(([-75.6784420145 45.4228387373], [-75.6819851277 45.4270238736], [-75.6761620215 45.4294520757], [-75.6726189083 45.4252671195], [-75.6784420145 45.4228387373]))"

coordinates = re.findall(r'(-?\d+\.\d+)\s(-?\d+\.\d+)', wkt)

# Convert to the desired tuple format
polygon_coords = [(float(lon), float(lat)) for lon, lat in coordinates]


lons = [pt[0] for pt in polygon_coords]
lats = [pt[1] for pt in polygon_coords]

min_lat = min(lats)
max_lat = max(lats)
min_lon = min(lons)
max_lon = max(lons)
folium_coords = [(lat, lon) for lon, lat in polygon_coords]

#  center for map
center_lat = sum([lat for lat, lon in folium_coords]) / len(folium_coords)
center_lon = sum([lon for lat, lon in folium_coords]) / len(folium_coords)

# Create folium map
m = folium.Map(location=(center_lat, center_lon), zoom_start=15)

# Add polygon to map
folium.Polygon(
    locations=folium_coords,
    color='black',
    weight=3,
    fill=True,
    fill_opacity=0.4
).add_to(m)

# Save map
m.save("custom_tilted_polygon_map.html")
display(m)

In [ ]:
#######   enforced constrain ======


import osmnx as ox
import folium
from shapely.geometry import Point, MultiPoint, LineString, MultiLineString
from shapely.ops import linemerge, nearest_points
from shapely.geometry import box
import numpy as np
import matplotlib.colors as mcolors
from sklearn.metrics.pairwise import haversine_distances
from sklearn.cluster import KMeans
from shapely import prepare, intersects


# Create the polygon
custom_polygon = Polygon(polygon_coords)

# Use it with OSMnx
tags = {'building': True}
buildings = ox.features_from_polygon(custom_polygon, tags=tags)

############
# polygon = box(min_lon, min_lat, max_lon, max_lat)

# tags = {'building': True}
# buildings = ox.features_from_polygon(polygon, tags=tags)

building_data = {}
for idx, (building_id, building) in enumerate(buildings.iterrows(), start=1):
    centroid = building.geometry.centroid
    building_data[f"b{idx}"] = {
        'lat': centroid.y,
        'lon': centroid.x,
        'geometry': centroid
    }


min_num = 7
max_num = 10

def enforce_cluster_sizes(coords, min_size=min_num, max_size=max_num, max_iter=20):
    coords_deg = np.degrees(coords)
    labels = np.arange(len(coords))
    next_label = len(coords)

    for _ in range(max_iter):
        unique_labels = np.unique(labels)
        new_labels = labels.copy()

        for label in unique_labels:
            indices = np.where(labels == label)[0]
            count = len(indices)

            if count > max_size:
                n_subclusters = (count + max_size - 1) // max_size
                sub_kmeans = KMeans(n_clusters=n_subclusters, random_state=42)
                sub_labels = sub_kmeans.fit_predict(coords_deg[indices])
                for i, idx in enumerate(indices):
                    new_labels[idx] = next_label + sub_labels[i]
                next_label += n_subclusters

        labels = new_labels.copy()
        unique_labels, counts = np.unique(labels, return_counts=True)
        small_clusters = unique_labels[counts < min_size]

        if len(small_clusters) == 0 and all(counts <= max_size):
            break

        for small_label in small_clusters:
            small_indices = np.where(labels == small_label)[0]
            other_indices = np.where(labels != small_label)[0]

            if len(other_indices) == 0:
                continue

            dists = haversine_distances(coords[small_indices], coords[other_indices])
            nearest_indices = np.argmin(dists, axis=1)
            nearest_labels = labels[other_indices][nearest_indices]

            most_common_label = np.bincount(nearest_labels).argmax()
            labels[small_indices] = most_common_label

    final_labels = labels.copy()
    while True:
        final_unique, final_counts = np.unique(final_labels, return_counts=True)
        oversized = [(label, count) for label, count in zip(final_unique, final_counts) if count > max_size]
        if not oversized:
            break
        for label, count in oversized:
            indices = np.where(final_labels == label)[0]
            n_subclusters = (count + max_size - 1) // max_size
            kmeans = KMeans(n_clusters=n_subclusters, random_state=10)
            sub_labels = kmeans.fit_predict(coords_deg[indices])
            for i, idx in enumerate(indices):
                final_labels[idx] = next_label + sub_labels[i]
            next_label += n_subclusters

    return final_labels

G = ox.graph.graph_from_bbox(bbox=(max_lon, min_lat, min_lon, max_lat), network_type="all", simplify=False, truncate_by_edge=True)
gdf_edges = ox.graph_to_gdfs(G, nodes=False, edges=True)
merged_lines = []
for street_name, group in gdf_edges.groupby('name', dropna=True):
    if not group.empty:
        merged = linemerge(group.geometry.tolist())
        if isinstance(merged, LineString):
            merged_lines.append(merged)
        elif isinstance(merged, MultiLineString):
            merged_lines.extend(list(merged.geoms))

all_streets = MultiLineString(merged_lines)
prepare(all_streets)

def perpendicular_projection(point, line):
    if isinstance(line, MultiLineString):
        nearest_line = None
        min_dist = float('inf')
        for component in line.geoms:
            dist = point.distance(component)
            if dist < min_dist:
                min_dist = dist
                nearest_line = component
        line = nearest_line
    nearest = line.interpolate(line.project(point))
    return nearest

for b, data in building_data.items():
    building_point = data['geometry']
    projected_point = perpendicular_projection(building_point, all_streets)
    data['street_point'] = {
        'lat': projected_point.y,
        'lon': projected_point.x,
        'geometry': projected_point
    }

projected_coords = np.radians(np.array([[data['street_point']['lat'], data['street_point']['lon']] for data in building_data.values()]))
cluster_labels = enforce_cluster_sizes(projected_coords, min_size=min_num, max_size=max_num)

unique_labels = np.unique(cluster_labels)
label_mapping = {old_label: new_label for new_label, old_label in enumerate(sorted(unique_labels))}
cluster_labels = np.array([label_mapping[label] for label in cluster_labels])

for i, (b, data) in enumerate(list(building_data.items())):
    building_data[b]['cluster'] = cluster_labels[i]
    building_data[f"b{i}"] = building_data.pop(b)

unique_clusters = set(cluster_labels)
colors = list(mcolors.TABLEAU_COLORS.values())
if len(unique_clusters) > len(colors):
    colors += list(mcolors.XKCD_COLORS.values())
cluster_colors = {cluster: colors[i % len(colors)] for i, cluster in enumerate(unique_clusters)}

cluster_centroids = {}
for cluster in unique_clusters:
    cluster_buildings = [data for b, data in building_data.items() if data['cluster'] == cluster]
    street_points = [data['street_point']['geometry'] for data in cluster_buildings]
    if len(street_points) > 1:
        street_centroid = MultiPoint(street_points).centroid
    else:
        street_centroid = street_points[0]
    street_centroid = perpendicular_projection(street_centroid, all_streets)
    cluster_centroids[cluster] = {
        'lat': street_centroid.y,
        'lon': street_centroid.x,
        'color': cluster_colors[cluster],
        'size': len(cluster_buildings),
        'buildings': [b for b in building_data if building_data[b]['cluster'] == cluster],
        'street_points': [data['street_point'] for data in cluster_buildings]
    }

m = folium.Map(location=[(min_lat + max_lat) / 2, (min_lon + max_lon) / 2], zoom_start=18, tiles='OpenStreetMap')

for b, data in building_data.items():
    cluster = data['cluster']
    folium.CircleMarker(location=[data['lat'], data['lon']], radius=3, color=cluster_colors[cluster], fill=True, fill_color=cluster_colors[cluster], fill_opacity=0.3, popup=f"Original Building {b} | Cluster {cluster}").add_to(m)

for b, data in building_data.items():
    cluster = data['cluster']
    folium.PolyLine(locations=[[data['lat'], data['lon']], [data['street_point']['lat'], data['street_point']['lon']]], color=cluster_colors[cluster], weight=1, opacity=0.5).add_to(m)

for cluster, centroid_data in cluster_centroids.items():
    for street_point in centroid_data['street_points']:
        folium.CircleMarker(location=[street_point['lat'], street_point['lon']], radius=1, color=cluster_colors[cluster], fill=True, fill_color=cluster_colors[cluster], fill_opacity=0.8, popup=f"Street Projection | Cluster {cluster}").add_to(m)



for cluster, centroid_data in cluster_centroids.items():
    popup_content = f"""
    <div style=\"font-family: Arial; font-size: 14px;\">
        <h4>Cluster {cluster}</h4>
        <p><strong>Buildings:</strong> {centroid_data['size']}</p>
        <p><strong>Building IDs:</strong> {', '.join(centroid_data['buildings'])}</p>
    </div>
    """
    folium.CircleMarker(location=[centroid_data['lat'], centroid_data['lon']], radius=10, color=cluster_colors[cluster], fill=True, fill_color=cluster_colors[cluster], fill_opacity=1, popup=folium.Popup(popup_content, max_width=300)).add_to(m)

# for cluster, centroid_data in cluster_centroids.items():
#     for street_point in centroid_data['street_points']:
#         folium.PolyLine(
#             locations=[
#                 [street_point['lat'], street_point['lon']],
#                 [centroid_data['lat'], centroid_data['lon']]
#             ],
#             color=cluster_colors[cluster],
#             weight=1.5,
#             opacity=0.7
#         ).add_to(m)

display(m)

print(f"\n{'='*40}")
print(f"{'CLUSTER STATISTICS':^40}")
print(f"{'='*40}")
print(f"Total buildings: {len(building_data)}")
print(f"Number of clusters: {len(set(cluster_labels))}")
print(f"\n{'Cluster':<10}{'Size':<10}{'Buildings':<20}")
print(f"{'-'*40}")

cluster_sizes = {label: np.sum(cluster_labels == label) for label in set(cluster_labels)}
for label in sorted(cluster_sizes.keys()):
    buildings = [b for b in building_data if building_data[b]['cluster'] == label]
    print(f"{label:<10}{cluster_sizes[label]:<10}{', '.join(buildings)}")



           CLUSTER STATISTICS           
Total buildings: 507
Number of clusters: 71

Cluster   Size      Buildings           
----------------------------------------
0         9         b1, b241, b244, b249, b279, b284, b294, b301, b364
1         10        b273, b278, b281, b298, b300, b378, b476, b477, b478, b479
2         7         b48, b49, b50, b51, b52, b475, b506
3         9         b78, b80, b81, b82, b84, b86, b124, b178, b179
4         10        b72, b83, b122, b125, b129, b135, b152, b170, b410, b411
5         8         b12, b31, b46, b316, b327, b328, b329, b330
6         8         b75, b154, b458, b459, b460, b461, b462, b465
7         10        b118, b158, b208, b209, b210, b211, b213, b289, b310, b442
8         10        b252, b297, b365, b366, b367, b368, b371, b372, b500, b501
9         10        b99, b114, b116, b128, b174, b183, b186, b437, b438, b439
10        9         b9, b134, b140, b151, b228, b229, b341, b346, b398
11        7         b101, b127, b394, b395, 

In [ ]:
# Print centroid coordinates for each cluster
for cluster in sorted(cluster_centroids.keys()):
    centroid_lat = cluster_centroids[cluster]['lat']
    centroid_lon = cluster_centroids[cluster]['lon']
    print(f"Cluster {cluster} Centroid: ({centroid_lat:.6f}, {centroid_lon:.6f})")




# projected points

from collections import defaultdict

# Grouping building IDs by cluster
cluster_building_ids = defaultdict(list)

for building_id, data in building_data.items():
    cluster = data['cluster']
    cluster_building_ids[cluster].append(building_id)

# Get street point coordinates for each cluster
cluster_coordinates = {}

for cluster, ids in cluster_building_ids.items():
    coordinates = [
        (
            building_data[building_id]['street_point']['lat'],
            building_data[building_id]['street_point']['lon']
        )
        for building_id in ids
    ]
    cluster_coordinates[cluster] = coordinates

# results sorted by cluster number
for cluster in sorted(cluster_coordinates.keys()):
    coords = cluster_coordinates[cluster]
    print(f"\n--- Cluster {cluster} ---")
    print(f"Number of points: {len(coords)}")
    for lat, lon in coords:
        print(f"Latitude: {lat}, Longitude: {lon}")



# buildings

clusters_coordinates = {}
for b_id, data in building_data.items():
    cluster = data['cluster']
    coord = (data['lat'], data['lon'])
    clusters_coordinates.setdefault(cluster, []).append(coord)

#  clusters in order with point numbers
for cluster in sorted(clusters_coordinates.keys()):
    print(f"\nCluster {cluster} (Total: {len(clusters_coordinates[cluster])}):")
    for i, (lat, lon) in enumerate(clusters_coordinates[cluster], start=1):
        print(f"  Point {i}: ({lat:.6f}, {lon:.6f})")



import pandas as pd
from collections import defaultdict

cluster_data = {}

for cluster in sorted(cluster_centroids.keys()):
    cluster_data[cluster] = {
        'centroid': (cluster_centroids[cluster]['lat'], cluster_centroids[cluster]['lon']),
        'buildings': [],
        'projected': []
    }

for b_id, data in building_data.items():
    cluster = data['cluster']

    building_coord = (data['lat'], data['lon'])

    projected_coord = (data['street_point']['lat'], data['street_point']['lon'])

    cluster_data[cluster]['buildings'].append(building_coord)
    cluster_data[cluster]['projected'].append(projected_coord)

rows = []
for cluster in sorted(cluster_data.keys()):
    centroid = cluster_data[cluster]['centroid']
    buildings = cluster_data[cluster]['buildings']
    projected = cluster_data[cluster]['projected']

    for b_coord, p_coord in zip(buildings, projected):
        rows.append({
            'Cluster ID': cluster,
            'Building Coordinates': f"({b_coord[0]:.6f}, {b_coord[1]:.6f})",
            'Projected Coordinates': f"({p_coord[0]:.6f}, {p_coord[1]:.6f})",
            'Centroid Coordinates': f"({centroid[0]:.6f}, {centroid[1]:.6f})"
        })

df = pd.DataFrame(rows)

df.to_csv('cluster_building_street_data.csv', index=False)

print("\nSample of the output data:")
print(df.head())

print("\nCluster Summary:")
for cluster in sorted(cluster_data.keys()):
    centroid_str = f"({cluster_data[cluster]['centroid'][0]:.6f}, {cluster_data[cluster]['centroid'][1]:.6f})"
    print(f"\nCluster {cluster} (Centroid: {centroid_str})")
    print(f"  Buildings: {len(cluster_data[cluster]['buildings'])}")
    print(f"  Projected street points: {len(cluster_data[cluster]['projected'])}")
    print("Sample projected point:", cluster_data[cluster]['projected'][0])


Cluster 0 Centroid: (45.424442, -75.678365)
Cluster 1 Centroid: (45.422984, -75.677957)
Cluster 2 Centroid: (45.423450, -75.676874)
Cluster 3 Centroid: (45.426873, -75.676414)
Cluster 4 Centroid: (45.427588, -75.674674)
Cluster 5 Centroid: (45.427564, -75.680651)
Cluster 6 Centroid: (45.425763, -75.674296)
Cluster 7 Centroid: (45.425275, -75.676260)
Cluster 8 Centroid: (45.424155, -75.678121)
Cluster 9 Centroid: (45.425957, -75.676102)
Cluster 10 Centroid: (45.425350, -75.679123)
Cluster 11 Centroid: (45.425623, -75.679356)
Cluster 12 Centroid: (45.427293, -75.678191)
Cluster 13 Centroid: (45.425232, -75.673853)
Cluster 14 Centroid: (45.424713, -75.673857)
Cluster 15 Centroid: (45.424995, -75.673193)
Cluster 16 Centroid: (45.425767, -75.675477)
Cluster 17 Centroid: (45.425394, -75.675161)
Cluster 18 Centroid: (45.424707, -75.675783)
Cluster 19 Centroid: (45.424953, -75.675989)
Cluster 20 Centroid: (45.425085, -75.674899)
Cluster 21 Centroid: (45.427623, -75.675860)
Cluster 22 Centroid:

In [ ]:
import osmnx as ox
import networkx as nx
import folium
import pandas as pd
import copy
from shapely.geometry import box, Point, LineString
import matplotlib.cm as cm
import matplotlib.colors as mcolors
from ast import literal_eval
from geopy.distance import geodesic





df = pd.read_csv('/content/cluster_building_street_data.csv')


df['Building Coordinates'] = df['Building Coordinates'].apply(literal_eval)
df['Projected Coordinates'] = df['Projected Coordinates'].apply(literal_eval)
df['Centroid Coordinates'] = df['Centroid Coordinates'].apply(literal_eval)


cluster_groups = df.groupby('Cluster ID')
cluster_routes = {
    cid: list(zip(group['Building Coordinates'], group['Projected Coordinates'], group['Centroid Coordinates']))
    for cid, group in cluster_groups
}


all_points = [pt for cluster in cluster_routes.values() for triple in cluster for pt in triple]
min_lat = min(p[0] for p in all_points) - 0.0005
max_lat = max(p[0] for p in all_points) + 0.0005
min_lon = min(p[1] for p in all_points) - 0.0005
max_lon = max(p[1] for p in all_points) + 0.0005
bounding_polygon = box(min_lon, min_lat, max_lon, max_lat)






G = ox.graph_from_polygon(bounding_polygon, network_type='drive', simplify=False, truncate_by_edge=True)
G = ox.distance.add_edge_lengths(G)
G = G.to_undirected()

def insert_point_on_edge(G, point_coords, connect_forward=True):
    point_geom = Point(point_coords[1], point_coords[0])  # (lon, lat)
    u, v, key = ox.distance.nearest_edges(G, point_coords[1], point_coords[0], return_dist=False)
    edge_data = G.edges[u, v, key]
    edge_geom = edge_data.get("geometry", LineString([
        (G.nodes[u]["x"], G.nodes[u]["y"]),
        (G.nodes[v]["x"], G.nodes[v]["y"])
    ]))

    projected_point = edge_geom.interpolate(edge_geom.project(point_geom))
    new_node_id = f"proj_{point_coords[0]}_{point_coords[1]}"
    if new_node_id in G.nodes:
        return new_node_id

    G.add_node(new_node_id, x=projected_point.x, y=projected_point.y)
    G.remove_edge(u, v, key=key)

    geom1 = LineString([Point(G.nodes[u]["x"], G.nodes[u]["y"]), projected_point])
    G.add_edge(u, new_node_id, length=geom1.length, geometry=geom1)
    G.add_edge(new_node_id, u, length=geom1.length, geometry=geom1)

    if connect_forward:
        geom2 = LineString([projected_point, Point(G.nodes[v]["x"], G.nodes[v]["y"])])
        G.add_edge(new_node_id, v, length=geom2.length, geometry=geom2)
        G.add_edge(v, new_node_id, length=geom2.length, geometry=geom2)

    return new_node_id

# Colors Per Cluster
cluster_ids = sorted(cluster_routes.keys())
colors = cm.get_cmap('tab10', len(cluster_ids))
color_map = {cid: mcolors.to_hex(colors(i)) for i, cid in enumerate(cluster_ids)}


map_center = list(cluster_routes.values())[0][0][0]
m = folium.Map(location=map_center, zoom_start=18)

for cid, triples in cluster_routes.items():
    route_color = color_map[cid]
    for building, projected, centroid in triples:
        # Draw markers
        folium.CircleMarker(building, radius=2, color=route_color, fill=True, tooltip="Building").add_to(m)
        # folium.CircleMarker(projected, radius=0.001, color=route_color, fill=True, tooltip="Projected").add_to(m)
        folium.CircleMarker(centroid, radius=7, color=route_color, fill=True, fill_opacity=0.9, tooltip="Centroid").add_to(m)

        # Building to Projected
        folium.PolyLine([building, projected], color=route_color, weight=2.5).add_to(m)

        try:
            G_temp = copy.deepcopy(G)

            p_node = insert_point_on_edge(G_temp, projected, connect_forward=True)
            c_node = insert_point_on_edge(G_temp, centroid, connect_forward=True)

            if p_node not in G_temp.nodes or c_node not in G_temp.nodes:
                raise ValueError(f"Nodes not in graph: {p_node}, {c_node}")

            path = nx.shortest_path(G_temp, p_node, c_node, weight='length')

            coords = []
            for n in path:
                node_data = G_temp.nodes[n]
                if 'x' not in node_data or 'y' not in node_data:
                    raise KeyError(f"Node {n} missing x/y")
                coords.append((node_data['y'], node_data['x']))

            folium.PolyLine(coords, color=route_color, weight=3.5, opacity=0.9).add_to(m)

        except Exception as e:
            print(f"Cluster {cid} routing error: {e}")

from IPython.display import display
display(m)


<ipython-input-5-9067fd1c2956>:79: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  colors = cm.get_cmap('tab10', len(cluster_ids))


In [ ]:
m.save('map10final.html')